In [1]:
#!/usr/bin/env python3
# -*- coding: utf-8 -*-
"""
Created on Mon Oct 29 19:39:21 2018

@author: abdolghaniebrahimi
"""
#########################################################
#regression with plain tensorflow using gradient descent#
########################################################

'\nCreated on Mon Oct 29 19:39:21 2018\n\n@author: abdolghaniebrahimi\n'

In [2]:
import numpy as np
import tensorflow as tf
from sklearn.datasets import fetch_california_housing
from sklearn.preprocessing import StandardScaler
import os
housing = fetch_california_housing()

checkpoint_path = "./model/model.cpkt"

/home/lab.analytics.northwestern.edu/gebrahimi/.conda/envs/snake/lib/python3.5/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


### Data normalization

In [3]:
#gradient descent needs data to be normalized
m , n = housing.data.shape
scaler = StandardScaler()
scaled_housing_data = scaler.fit_transform(housing.data)
scaled_housing_data_plus_bias = np.c_[np.ones((m, 1)), scaled_housing_data]

### batch maker

In [4]:
# function for randomly choosing a batch of size batch size
def fetch_batch(epoch, batch_index, batch_size):
    indices = np.random.randint(m, size=batch_size)  
    X_batch = scaled_housing_data_plus_bias[indices] 
    y_batch = housing.target.reshape(-1, 1)[indices] 
    return X_batch, y_batch

### Construction

In [5]:
#reset the graph
tf.reset_default_graph()


# training parameters
n_epochs = 1000
learning_rate = 0.01
batch_size = 100
n_batches = int(np.ceil(m / batch_size))



#We use placeholder whenever we need to feed data to a graph
#It allows us to create our operations and build our computation graph, without needing the data
X = tf.placeholder(tf.float32, shape=(None, n + 1), name="X") #the first element is always set to None and it related to batch_size which could change in different training epochs.
y = tf.placeholder(tf.float32, shape=(None, 1), name="y")


theta = tf.Variable(tf.random_uniform([n + 1, 1], -1.0, 1.0, seed=42), name="theta")
y_pred = tf.matmul(X, theta, name="predictions")
error = y_pred - y
mse = tf.reduce_mean(tf.square(error), name="mse") #defines the error
optimizer = tf.train.GradientDescentOptimizer(learning_rate=learning_rate) #construct an optimizer. This one is gradient descent but you can have RMSprop or Adam or other types.
training_op = optimizer.minimize(mse) #taking the optimization step. (here the gradient descent step)

### FYI

In [6]:
##################################################################################################################################
# this part has nothing to do with overall code and training the model but just for your information on how to take the gradients#
# I am taking the gradients but never use it manually myself. The training_op code line apply gradients automatically.
grads = tf.gradients(mse, theta)
##################################################################################################################################

### Execution

In [ ]:
#initialize all the values
init = tf.global_variables_initializer()


#build a saver
saver = tf.train.Saver()
with tf.Session() as sess:
    if os.path.isfile(checkpoint_path + ".index"):
        saver.restore(sess, checkpoint_path)
    else:
        sess.run(init)

    for epoch in range(n_epochs):
        print("###################################################")
        for batch_index in range(n_batches):
            X_batch, y_batch = fetch_batch(epoch, batch_index, batch_size)
            _, loss, gradients = sess.run([training_op, mse, grads], feed_dict={X: X_batch, y: y_batch})
            print("Loss for epoch {} and batch index {} is {}".format(epoch, batch_index, loss))
            
            if epoch % 100 == 0:
                saver.save(sess, "./model/model.ckpt")
                print("Model Saved")
    best_theta = theta.eval()

###################################################
Loss for epoch 0 and batch index 0 is 2.4050683975219727
Model Saved
Loss for epoch 0 and batch index 1 is 2.2594330310821533
Model Saved
Loss for epoch 0 and batch index 2 is 2.0460269451141357
Model Saved
Loss for epoch 0 and batch index 3 is 2.4035818576812744
Model Saved
Loss for epoch 0 and batch index 4 is 2.062870502471924
Model Saved
Loss for epoch 0 and batch index 5 is 2.1734120845794678
Model Saved
Loss for epoch 0 and batch index 6 is 2.0633323192596436
Model Saved
Loss for epoch 0 and batch index 7 is 2.143523693084717
Model Saved
Loss for epoch 0 and batch index 8 is 1.948591709136963
Model Saved
Loss for epoch 0 and batch index 9 is 1.9253987073898315
Model Saved
Loss for epoch 0 and batch index 10 is 1.682183861732483
Model Saved
Loss for epoch 0 and batch index 11 is 1.5113459825515747
Model Saved
Loss for epoch 0 and batch index 12 is 1.6508581638336182
Model Saved
Loss for epoch 0 and batch index 13 is 1.71909189224